# Qiskit Chemistry on CoCalc

Python 3, Ubuntu Linux kernel

https://github.com/Qiskit/qiskit-chemistry

In [2]:
from qiskit_chemistry import FermionicOperator
from qiskit_chemistry.drivers import PySCFDriver, UnitsType

In [3]:
# Use PySCF, a classical computational chemistry software package, to compute the one-body and two-body integrals in
# molecular-orbital basis, necessary to form the Fermionic operator
driver = PySCFDriver(
    atom='H .0 .0 .0; H .0 .0 0.735', unit=UnitsType.ANGSTROM, basis='sto3g')
molecule = driver.run()
num_particles = molecule.num_alpha + molecule.num_beta
num_spin_orbitals = molecule.num_orbitals * 2
num_spin_orbitals

4

In [11]:
# Build the qubit operator, which is the input to the VQE algorithm in Aqua
ferOp = FermionicOperator(h1=molecule.one_body_integrals, h2=molecule.two_body_integrals)
map_type = 'PARITY'
qubitOp = ferOp.mapping(map_type)
qubitOp = qubitOp.two_qubit_reduced_operator(num_particles)
num_qubits = qubitOp.num_qubits

# set the backend for the quantum computation
from qiskit import BasicAer as Aer
backend = Aer.get_backend('statevector_simulator')

# setup a classical optimizer for VQE
from qiskit_aqua.components.optimizers import L_BFGS_B
optimizer = L_BFGS_B()

# setup the initial state for the variational form
from qiskit_chemistry.aqua_extensions.components.initial_states import HartreeFock
init_state = HartreeFock(num_qubits, num_spin_orbitals, num_particles)

# setup the variational form for VQE
from qiskit_aqua.components.variational_forms import RYRZ
var_form = RYRZ(num_qubits, initial_state=init_state)

# setup and run VQE
from qiskit_aqua.algorithms import VQE
algorithm = VQE(qubitOp, var_form, optimizer)
result = algorithm.run(backend)
print(result['energy'])

-1.8572750301661332


In [9]:
from pprint import pprint
pprint(result)

{'eigvals': array([-1.83696799]),
 'eigvecs': array([[0.+0.j, 1.+0.j, 0.+0.j, 0.+0.j]]),
 'energy': -1.8369679912029846,
 'eval_count': 51,
 'eval_time': 1.8833088874816895,
 'opt_params': array([ 3.14159265,  3.14159265,  3.14159265,  3.14159265, -3.14159265,
       -3.14159265,  3.14159265, -0.21256805,  3.14159265,  3.14159265,
        3.14159265,  3.14159265, -3.14159265, -3.14159265,  3.14159265,
        3.14159265])}
